In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/jigsaw-toxic-comment-classification-challenge/train.csv.zip
/kaggle/input/jigsaw-toxic-comment-classification-challenge/sample_submission.csv.zip
/kaggle/input/jigsaw-toxic-comment-classification-challenge/test_labels.csv.zip
/kaggle/input/jigsaw-toxic-comment-classification-challenge/test.csv.zip


In [2]:
import pandas as pd

df = pd.read_csv("/kaggle/input/jigsaw-toxic-comment-classification-challenge/train.csv.zip")
df.head()  # Display the first few rows


id                                       comment_text  toxic  \
0  0000997932d777bf  Explanation\nWhy the edits made under my usern...      0   
1  000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0   
2  000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0   
3  0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0   
4  0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0

In [3]:
import os
import pandas as pd
import tensorflow as tf
import numpy as np

In [4]:
df.shape

(159571, 8)

In [5]:
df.iloc[7]['comment_text']

"Your vandalism to the Matt Shirvington article has been reverted.  Please don't do it again, or you will be banned."

In [6]:
df[df.columns[2:]].iloc[7]

toxic            0
severe_toxic     0
obscene          0
threat           0
insult           0
identity_hate    0
Name: 7, dtype: int64

In [7]:
from tensorflow.keras.layers import TextVectorization

In [8]:
df.columns

Index(['id', 'comment_text', 'toxic', 'severe_toxic', 'obscene', 'threat',
       'insult', 'identity_hate'],
      dtype='object')

In [9]:
X = df['comment_text']
y = df[df.columns[2:]].values

In [10]:
y

array([[0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       ...,
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]])

In [11]:
# how many word we want to stored in our vocab or number of words in the vocab
MAX_FEATURES = 200000

In [12]:
# output_sequence_length = 1800 -> use to give same lenght to each comment or paragraph like if 1. contain 3 word and 2. contain 2 word so it convert 
# that 2 word to 3 by adding 0 at last , output_mode -> assign word a integer value like tea - 2, me -5, you - 1
vectorizer = TextVectorization(max_tokens = MAX_FEATURES,output_sequence_length = 1800, output_mode = 'int')

In [13]:
# tech our model a vocabulary adapt going to learn all the word inside the X and X.values is use to convert this into numpy 
vectorizer.adapt(X.values)

In [14]:
vectorizer.get_vocabulary(include_special_tokens=True)

['',
 '[UNK]',
 'the',
 'to',
 'of',
 'and',
 'a',
 'you',
 'i',
 'is',
 'that',
 'in',
 'it',
 'for',
 'this',
 'not',
 'on',
 'be',
 'as',
 'have',
 'are',
 'your',
 'with',
 'if',
 'article',
 'was',
 'or',
 'but',
 'page',
 'my',
 'an',
 'from',
 'by',
 'do',
 'at',
 'about',
 'me',
 'so',
 'wikipedia',
 'can',
 'what',
 'there',
 'all',
 'has',
 'will',
 'talk',
 'please',
 'would',
 'its',
 'no',
 'one',
 'just',
 'like',
 'they',
 'he',
 'dont',
 'which',
 'any',
 'been',
 'should',
 'more',
 'we',
 'some',
 'other',
 'who',
 'see',
 'here',
 'also',
 'his',
 'think',
 'im',
 'because',
 'know',
 'how',
 'am',
 'people',
 'why',
 'edit',
 'articles',
 'only',
 'out',
 'up',
 'when',
 'were',
 'use',
 'then',
 'may',
 'time',
 'did',
 'them',
 'now',
 'being',
 'their',
 'than',
 'thanks',
 'even',
 'get',
 'make',
 'good',
 'had',
 'very',
 'information',
 'does',
 'could',
 'well',
 'want',
 'such',
 'sources',
 'way',
 'name',
 'these',
 'deletion',
 'pages',
 'first',
 'help'

In [15]:
vocab = vectorizer.get_vocabulary(include_special_tokens=True)

In [16]:
word_to_index = {word: index for index, word in enumerate(vocab)}
print(word_to_index) 

{'': 0, '[UNK]': 1, 'the': 2, 'to': 3, 'of': 4, 'and': 5, 'a': 6, 'you': 7, 'i': 8, 'is': 9, 'that': 10, 'in': 11, 'it': 12, 'for': 13, 'this': 14, 'not': 15, 'on': 16, 'be': 17, 'as': 18, 'have': 19, 'are': 20, 'your': 21, 'with': 22, 'if': 23, 'article': 24, 'was': 25, 'or': 26, 'but': 27, 'page': 28, 'my': 29, 'an': 30, 'from': 31, 'by': 32, 'do': 33, 'at': 34, 'about': 35, 'me': 36, 'so': 37, 'wikipedia': 38, 'can': 39, 'what': 40, 'there': 41, 'all': 42, 'has': 43, 'will': 44, 'talk': 45, 'please': 46, 'would': 47, 'its': 48, 'no': 49, 'one': 50, 'just': 51, 'like': 52, 'they': 53, 'he': 54, 'dont': 55, 'which': 56, 'any': 57, 'been': 58, 'should': 59, 'more': 60, 'we': 61, 'some': 62, 'other': 63, 'who': 64, 'see': 65, 'here': 66, 'also': 67, 'his': 68, 'think': 69, 'im': 70, 'because': 71, 'know': 72, 'how': 73, 'am': 74, 'people': 75, 'why': 76, 'edit': 77, 'articles': 78, 'only': 79, 'out': 80, 'up': 81, 'when': 82, 'were': 83, 'use': 84, 'then': 85, 'may': 86, 'time': 87, 'di

In [17]:
vectorizer('Hello world, life is not that much great')[:7]

<tf.Tensor: shape=(7,), dtype=int64, numpy=array([288, 263, 306,   9,  15,  10, 129])>

In [18]:
vectorizer('Hello world life')[:3]

<tf.Tensor: shape=(3,), dtype=int64, numpy=array([288, 263, 306])>

In [19]:
vectorized_text = vectorizer(X.values)

In [20]:
vectorized_text

<tf.Tensor: shape=(159571, 1800), dtype=int64, numpy=
array([[  645,    76,     2, ...,     0,     0,     0],
       [    1,    54,  2489, ...,     0,     0,     0],
       [  425,   441,    70, ...,     0,     0,     0],
       ...,
       [32445,  7392,   383, ...,     0,     0,     0],
       [    5,    12,   534, ...,     0,     0,     0],
       [    5,     8,   130, ...,     0,     0,     0]])>

In [21]:
# we creating the datapipeline  MCSHBAP - Map, Cache, shuffle, Batch, prefetch
import tensorflow as tf
dataset = tf.data.Dataset.from_tensor_slices((vectorized_text, y))
dataset = dataset.cache()
dataset = dataset.shuffle(160000)
dataset = dataset.batch(16)
dataset = dataset.prefetch(8)

In [22]:
dataset.as_numpy_iterator().next()

(array([[    2,   234,     8, ...,     0,     0,     0],
        [66037, 11604,  1419, ...,     0,     0,     0],
        [  283,    16,  1381, ...,     0,     0,     0],
        ...,
        [   65,    67,  6480, ...,     0,     0,     0],
        [  704,   122,     3, ...,     0,     0,     0],
        [ 3662,    36,    44, ...,     0,     0,     0]]),
 array([[0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [1, 0, 1, 0, 1, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [1, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0]]))

In [23]:
batch_X, batch_y = dataset.as_numpy_iterator().next()

In [24]:
dataset

<_PrefetchDataset element_spec=(TensorSpec(shape=(None, 1800), dtype=tf.int64, name=None), TensorSpec(shape=(None, 6), dtype=tf.int64, name=None))>

In [25]:
# Now to divide our data into train , test and validation
len(dataset) # this come in batch so that mean we have 9974 batch

9974

In [26]:
train = dataset.take(int(len(dataset)*.7))
val = dataset.skip(int(len(dataset)*.7)).take(int(len(dataset)*.2))
test = dataset.skip(int(len(dataset)*.9)).take(int(len(dataset)*.1))

In [27]:
train_generator = train.as_numpy_iterator()

In [28]:
train_generator.next()

(array([[  454,   157,     3, ...,     0,     0,     0],
        [  185,    14,    59, ...,     0,     0,     0],
        [    8,   483,    17, ...,     0,     0,     0],
        ...,
        [ 1637,   206,   920, ...,     0,     0,     0],
        [90727,   405,    13, ...,     0,     0,     0],
        [  433,   253,     9, ...,     0,     0,     0]]),
 array([[0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0]]))

In [29]:

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dropout, Bidirectional, Dense, Embedding

In [30]:
model = Sequential()
model.add(Embedding(input_dim=MAX_FEATURES + 1, output_dim=32))
model.add(Bidirectional(LSTM(32, activation = 'tanh')))
model.add(Dense(128, activation ='relu'))
model.add(Dense(256, activation ='relu'))
model.add(Dense(128, activation ='relu'))
model.add(Dense(6, activation ='sigmoid'))

model.build(input_shape=(None, None))

In [31]:
model.compile(loss='BinaryCrossentropy', optimizer ='Adam')

In [32]:
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ embedding (Embedding)                │ (None, None, 32)            │       6,400,032 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ bidirectional (Bidirectional)        │ (None, 64)                  │          16,640 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 128)                 │           8,320 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_1 (Dense)                      │ (None, 256)                 │          33,024 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_2 (Dense)                      │ (None, 128)                 │          32,896 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_3 (Dense)                      │ (None, 6)                   │             774 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 6,491,686 (24.76 MB)

 Trainable params: 6,491,686 (24.76 MB)

 Non-trainable params: 0 (0.00 B)

In [33]:
print("Train size:", train.cardinality().numpy())
print("Validation size:", val.cardinality().numpy())
print("Test size:", test.cardinality().numpy())

Train size: 6981
Validation size: 1994
Test size: 997


In [34]:
histroy = model.fit(train, epochs = 1, validation_data=val)

6981/6981 ━━━━━━━━━━━━━━━━━━━━ 615s 88ms/step - loss: 0.0840 - val_loss: 0.0449


In [35]:
import matplotlib.pyplot as plt

In [38]:
History.histroy

NameError: name 'History' is not defined

In [ ]:
plt.figure(figsize=(8,5))
pd.DataFrame(history.histroy).plot()
plt.show()

3. Make Predictions

In [60]:
input_text = vectorizer('I love your work')

In [61]:
model.predict(np.expand_dims(input_text,0))

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step


array([[0.05179151, 0.00104649, 0.01365481, 0.00318022, 0.01605391,
        0.00541991]], dtype=float32)

In [62]:
df.columns[2:]

Index(['toxic', 'severe_toxic', 'obscene', 'threat', 'insult',
       'identity_hate'],
      dtype='object')

In [63]:
res = model.predict(np.expand_dims(input_text,0))

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step


In [48]:
batch = test.as_numpy_iterator().next()

In [58]:
batch

(array([[  167,     4,   657, ...,     0,     0,     0],
        [    8,   253,    22, ...,     0,     0,     0],
        [  803,   468,   179, ...,     0,     0,     0],
        ...,
        [   85,     7,   119, ...,     0,     0,     0],
        [  103,   154,    46, ...,     0,     0,     0],
        [    5,    70, 29778, ...,     0,     0,     0]]),
 array([[0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0]]))

In [49]:
batch_X,batch_y = test.as_numpy_iterator().next()

In [57]:
batch_y

array([[0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [1, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]])

In [65]:
(model.predict(batch_X)>0.5).astype(int)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step


array([[0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [1, 0, 1, 0, 1, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]])

4. Evaluate Model****

In [51]:
from tensorflow.keras.metrics import Precision, Recall, CategoricalAccuracy

In [52]:
pre = Precision()
re = Recall()
acc = CategoricalAccuracy()

In [99]:
from tensorflow.keras.metrics import Precision, Recall, CategoricalAccuracy

pre = Precision()
re = Recall()
acc = CategoricalAccuracy()

for batch in test.as_numpy_iterator():
    # Unpack batch
    X_true, y_true = batch

    # Predict
    yhat = model.predict(X_true)

    # Flatten and threshold
    y_true = y_true.flatten()
    yhat = (yhat.flatten() > 0.5).astype(int)

    # Update metrics
    pre.update_state(y_true, yhat)
    re.update_state(y_true, yhat)
    acc.update_state(y_true, yhat)



1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━

In [100]:
print(f'Precision:{pre.result().numpy()}, Recall:{re.result().numpy()}, Accuracy:{acc.result().numpy()}')

Precision:0.8285192251205444, Recall:0.6782400608062744, Accuracy:0.7352055907249451


****5. Test and Gradio

In [101]:
#!pip install gradio

In [102]:
import tensorflow as tf
import gradio as gr

In [103]:
# model.save('toxicity_model.h5')

In [104]:
# model = tf.keras.models.load_model('toxicity_model.h5')

In [105]:
input_value = vectorizer('Hey I hate you! and i promise i gonna hurt you down')

In [106]:
res = model.predict(np.expand_dims(input_value,0))

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step


In [107]:
res

array([[0.61477566, 0.01405949, 0.18478224, 0.0148624 , 0.2492129 ,
        0.03522645]], dtype=float32)

In [108]:
def score_comment(comment):
    vectorized_comment = vectorizer([comment])
    results = model.predict(vectorized_comment)

    text = ''
    for idx, col in enumerate(df.columns[2:]):
        text += '{}: {}\n'.format(col, results[0][idx]>0.5)

    return text

In [109]:
interface = gr.Interface(fn=score_comment,
                        inputs = gr.Textbox(lines=3, placeholder ='Comment to see'),
                        outputs='text')

In [110]:
interface.launch(share=True)

* Running on local URL:  http://127.0.0.1:7863
* Running on public URL: https://295ef1b50feee38f69.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
